<a href="https://colab.research.google.com/github/Bromus001/notebooks/blob/master/Segmenting_and_Clustering_Neighborhoods_in_Toronto.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Part of Coursera MOOC

In [5]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

from bs4 import BeautifulSoup
import requests

print('Libraries imported.')

Libraries imported.


In [0]:
# Create URL and retrieve page markup
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"

page_response = requests.get(url, timeout=5)

page_content = BeautifulSoup(page_response.content, "html.parser")

In [0]:
# Extract the table and rows list
table_data = page_content.find("table")

table_body = table_data.find("tbody")  

rows = table_body.find_all("tr")

In [0]:
# Iterate rows extracting data from cells
data = []

first_row=True

for row in rows:
  
  if first_row:
    cols = row.find_all("th")
    headers = [element.text.strip() for element in cols]
    first_row=False
    continue
  
  cols = row.find_all("td")  
  cols = [element.text.strip() for element in cols]  
  data.append(cols)

In [61]:
# Create DataFrame an remove undesired rows
df_data = pd.DataFrame(data, columns=headers)

df_data = df_data[df_data["Borough"]!="Not assigned"].copy().reset_index(drop=True)

df_data.head()

Postcode           Borough     Neighbourhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M5A  Downtown Toronto       Regent Park
4      M6A        North York  Lawrence Heights

In [62]:
# Shape of the DataFrame
df_data.shape

(212, 3)

In [55]:
# Get the Geolocalization data
df_geo = pd.read_csv("https://cocl.us/Geospatial_data")
df_geo.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [63]:
# Merge datasets
df_data = df_data.merge(df_geo, how="left", left_on="Postcode", right_on="Postal Code").drop(columns=["Postal Code"])
df_data.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636
4      M6A        North York  Lawrence Heights  43.718518 -79.464763

In [66]:
# Get Lat & Lng of Toronto City
address = 'Toronto, ON'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))

/usr/local/lib/python3.6/dist-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of Toronto City are 43.653963, -79.387207.


In [72]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_data['Latitude'], df_data['Longitude'], df_data['Borough'], df_data['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill_color='#3186cc').add_to(map_toronto)  
    
map_toronto

In [0]:
CLIENT_ID = 'XXX' # your Foursquare ID
CLIENT_SECRET = 'XXX' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

In [0]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        #try:
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']

        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

        #except:
        #    pass
        
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']

    return(nearby_venues)

In [133]:
toronto_venues = getNearbyVenues(names=df_data['Neighbourhood'],
                                   latitudes=df_data['Latitude'],
                                   longitudes=df_data['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Regent Park
Lawrence Heights
Lawrence Manor
Not assigned
Islington Avenue
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design E

In [134]:
print(toronto_venues.shape)
toronto_venues.head()

(4437, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1                     KFC       43.754387       -79.333021   
2           Variety Store       43.751974       -79.333114   
3  Victoria Village Arena       43.723481       -79.315635   
4             Tim Hortons       43.725517       -79.313103   

         Venue Category  
0                  Park  
1  Fast Food Restaurant  
2     Food & Drink Shop  
3          Hockey Arena  
4           Coffee Shop

In [123]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                              
Adelaide                                                            100   
Agincourt                                                             5   
Agincourt North                                                       2   
Albion Gardens                                                       11   
Alderwood                                                             8   
Bathurst Manor                                                       16   
Bathurst Quay                                                        14   
Bayview Village                                                       4   
Beaumond Heights                                                     11   
Bedford Park                                                         26   
Berczy Park                                                          55   
Birch Cliff                                                           4   
Bloordale Gardens                                                     6   
Brockton                                                             20   
Business reply mail Processing Centre969 Eastern                     17   
CFB Toronto                                                           4   
CN Tower                                                             14   
Cabbagetown                                                          46   
Caledonia-Fairbanks                                                   6   
Canada Post Gateway Processing Centre                                11   
Cedarbrae                                                             7   
Central Bay Street                                                   84   
Chinatown                                                            97   
Christie                                                             15   
Church and Wellesley                                                 82   
Clairlea                                                             10   
Clarks Corners                                                        9   
Cliffcrest                                                            2   
Cliffside                                                             2   
Cliffside West                                                        4   
Cloverdale                                                            2   
Commerce Court                                                      100   
Davisville                                                           34   
Davisville North                                                      7   
Deer Park                                                            14   
Del Ray                                                               4   
Design Exchange                                                     100   
Don Mills North                                                       5   
Don Mills South                                                      20   
Dorset Park                                                           6   
Dovercourt Village                                                   21   
Downsview Central                                                     4   
Downsview East                                                        4   
Downsview North                                                      16   
Downsview Northwest                                                   5   
Downsview West                                                        5   
Dufferin                                                             21   
East Birchmount Park                                                  6   
East Toronto                                                          4   
Emery                                                                 4   
Eringate                                                              6   
Exhibition Place                                                     20   


In [149]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 
toronto_onehot['Neighborhood Latitude'] = toronto_venues['Neighborhood Latitude'] 
toronto_onehot['Neighborhood Longitude'] = toronto_venues['Neighborhood Longitude'] 

	

# move neighborhood column to the first column
fixed_columns = ["Neighborhood", "Neighborhood Latitude", "Neighborhood Longitude"] + [col for col in toronto_onehot.columns.tolist() if col not in ["Neighborhood", "Neighborhood Latitude", "Neighborhood Longitude"]]

toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

   Accessories Store  Adult Boutique  Afghan Restaurant  Airport  \
0                  0               0                  0        0   
1                  0               0                  0        0   
2                  0               0                  0        0   
3                  0               0                  0        0   
4                  0               0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Belgian Restaurant  \
0                   0      0         0           0                   0   
1                   0      0         0           0                   0   
2                   0      0         0           0                   0   
3                   0      0         0           0                   0   
4                   0      0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0  

In [151]:
# Grouping by Neighborhood and calculate the mean of the frecuency of each venue
toronto_grouped = toronto_onehot.groupby(["Neighborhood", "Neighborhood Latitude", "Neighborhood Longitude"]).mean().reset_index()
toronto_grouped

Neighborhood  Neighborhood Latitude  \
0                                            Adelaide              43.650571   
1                                           Agincourt              43.794200   
2                                     Agincourt North              43.815252   
3                                      Albion Gardens              43.739416   
4                                           Alderwood              43.602414   
5                                      Bathurst Manor              43.754328   
6                                       Bathurst Quay              43.628947   
7                                     Bayview Village              43.786947   
8                                    Beaumond Heights              43.739416   
9                                        Bedford Park              43.733283   
10                                        Berczy Park              43.644771   
11                                        Birch Cliff              43.692657   
12                                  Bloordale Gardens              43.643515   
13                                           Brockton              43.636847   
14   Business reply mail Processing Centre969 Eastern              43.662744   
15                                        CFB Toronto              43.737473   
16                                           CN Tower              43.628947   
17                                        Cabbagetown              43.667967   
18                                Caledonia-Fairbanks              43.689026   
19              Canada Post Gateway Processing Centre              43.636966   
20                                          Cedarbrae              43.773136   
21                                 Central Bay Street              43.657952   
22                                          Chinatown              43.653206   
23                                           Christie              43.669542   
24                               Church and Wellesley              43.665860   
25                                           Clairlea              43.711112   
26                                     Clarks Corners              43.781638   
27                                         Cliffcrest              43.716316   
28                                          Cliffside              43.716316   
29                                     Cliffside West              43.692657   
30                                         Cloverdale              43.650943   
31                                     Commerce Court              43.648198   
32                                         Davisville              43.704324   
33                                   Davisville North              43.712751   
34                                          Deer Park              43.686412   
35                                            Del Ray              43.691116   
36                                    Design Exchange              43.647177   
37                                    Don Mills North              43.745906   
38                                    Don Mills South              43.725900   
39                                        Dorset Park              43.757410   
40                                 Dovercourt Village              43.669005   
41                                  Downsview Central              43.728496   
42                                     Downsview East              43.737473   
43                                    Downsview North              43.754328   
44                                Downsview Northwest              43.761631   
45                                     Downsview West              43.739015   
46                                           Dufferin              43.669005   
47                               East Birchmount Park              43.727929   
48                                       East Toronto              43.685347   
49                                       

In [0]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[3:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [161]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood  \
0                                            Adelaide   
1                                           Agincourt   
2                                     Agincourt North   
3                                      Albion Gardens   
4                                           Alderwood   
5                                      Bathurst Manor   
6                                       Bathurst Quay   
7                                     Bayview Village   
8                                    Beaumond Heights   
9                                        Bedford Park   
10                                        Berczy Park   
11                                        Birch Cliff   
12                                  Bloordale Gardens   
13                                           Brockton   
14   Business reply mail Processing Centre969 Eastern   
15                                        CFB Toronto   
16                                           CN Tower   
17                                        Cabbagetown   
18                                Caledonia-Fairbanks   
19              Canada Post Gateway Processing Centre   
20                                          Cedarbrae   
21                                 Central Bay Street   
22                                          Chinatown   
23                                           Christie   
24                               Church and Wellesley   
25                                           Clairlea   
26                                     Clarks Corners   
27                                         Cliffcrest   
28                                          Cliffside   
29                                     Cliffside West   
30                                         Cloverdale   
31                                     Commerce Court   
32                                         Davisville   
33                                   Davisville North   
34                                          Deer Park   
35                                            Del Ray   
36                                    Design Exchange   
37                                    Don Mills North   
38                                    Don Mills South   
39                                        Dorset Park   
40                                 Dovercourt Village   
41                                  Downsview Central   
42                                     Downsview East   
43                                    Downsview North   
44                                Downsview Northwest   
45                                     Downsview West   
46                                           Dufferin   
47                               East Birchmount Park   
48                                       East Toronto   
49                                              Emery   
50                                           Eringate   
51                                   Exhibition Place   
52                                           Fairview   
53                               First Canadian Place   
54                                    Flemingdon Park   
55                                  Forest Hill North   
56                                     Forest Hill SE   
57                                   Forest Hill West   
58                                    Garden District   
59                                          Glencairn   
60                                        Golden Mile   
61                                        Grange Park   
62                                          Guildwood   
63                                            Harbord   
64                                       Harbourfront   
65                                  Harbourfront East   
66                                  Harbourfront West   
67                                         Henry Farm   
68                                          High Park   
69                                     Highland Cre

In [162]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 4, 0, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [164]:
toronto_merged = df_data[df_data["Neighbourhood"].isin(toronto_grouped["Neighborhood"].values.tolist())]
toronto_merged.rename(columns={"Neighbourhood":"Neighborhood"}, inplace=True)

# add clustering labels
toronto_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:3027: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  return super(DataFrame, self).rename(**kwargs)
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """


Postcode           Borough      Neighborhood   Latitude  Longitude  \
0      M3A        North York         Parkwoods  43.753259 -79.329656   
1      M4A        North York  Victoria Village  43.725882 -79.315572   
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636   
4      M6A        North York  Lawrence Heights  43.718518 -79.464763   

   Cluster Labels   1st Most Common Venue  2nd Most Common Venue  \
0               1    Fast Food Restaurant                   Park   
1               4             Pizza Place  Portuguese Restaurant   
2               0             Coffee Shop                   Café   
3               1             Coffee Shop                   Café   
4               1  Furniture / Home Store         Clothing Store   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
0     Food & Drink Shop  Eastern European Restaurant        Discount Store   
1           Coffee Shop                 Hockey Arena          Intersection   
2                  Park                       Bakery                   Pub   
3                  Park                       Bakery                   Pub   
4           Coffee Shop                     Boutique    Athletics & Sports   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0               Dog Run      Doner Restaurant            Donut Shop   
1            Comic Shop          Dessert Shop           Event Space   
2        Breakfast Spot    Mexican Restaurant               Theater   
3        Breakfast Spot    Mexican Restaurant               Theater   
4    Miscellaneous Shop            Shoe Store     Accessories Store   

   9th Most Common Venue 10th Most Common Venue  
0              Drugstore    Dumpling Restaurant  
1   Ethiopian Restaurant    Empanada Restaurant  
2  Performing Arts Venue                Brewery  
3  Performing Arts Venue                Brewery  
4  Vietnamese Restaurant            Event Space

In [167]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters